In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import numpy as np
import pandas as pd
import re
import nltk
import spacy
import string
pd.options.mode.chained_assignment = None

In [ ]:
import numpy as np
import pandas as pd
import pickle
import tensorflow as tf
from wordcloud import WordCloud, STOPWORDS
import matplotlib.pyplot as plt
from tensorflow.keras.preprocessing import text, sequence
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Activation
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import Conv1D, GlobalMaxPooling1D, MaxPooling1D
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, confusion_matrix
import seaborn as sns
plt.style.use('fivethirtyeight')
print(tf.__version__)


2.7.0


In [ ]:
full_df = pd.read_csv("/content/drive/MyDrive/BITS/4-1/Projects/Nlp/hateval2019_en_train.csv")
df = full_df[["text"]]
df["text"] = df["text"].astype(str)
full_df.head()

id                                               text  HS  TR  AG
0  201  Hurray, saving us $$$ in so many ways @potus @...   1   0   0
1  202  Why would young fighting age men be the vast m...   1   0   0
2  203  @KamalaHarris Illegals Dump their Kids at the ...   1   0   0
3  204  NY Times: 'Nearly All White' States Pose 'an A...   0   0   0
4  205  Orban in Brussels: European leaders are ignori...   0   0   0

REMOVE USERNAME

In [ ]:
import re

def remove_usernames_links(tweet):
    tweet = re.sub('@[^\s]+','',tweet)
    tweet = re.sub('http[^\s]+','',tweet)
    return tweet

df['tweet'] = df["text"].apply(remove_usernames_links)
df.head()

text                                              tweet
0  Hurray, saving us $$$ in so many ways @potus @...  Hurray, saving us $$$ in so many ways   #LockT...
1  Why would young fighting age men be the vast m...  Why would young fighting age men be the vast m...
2  @KamalaHarris Illegals Dump their Kids at the ...   Illegals Dump their Kids at the border like R...
3  NY Times: 'Nearly All White' States Pose 'an A...  NY Times: 'Nearly All White' States Pose 'an A...
4  Orban in Brussels: European leaders are ignori...  Orban in Brussels: European leaders are ignori...

LOWER CASING

In [ ]:
df["text_lower"] = df["tweet"].str.lower()
df.head()

text  ...                                         text_lower
0  Hurray, saving us $$$ in so many ways @potus @...  ...  hurray, saving us $$$ in so many ways   #lockt...
1  Why would young fighting age men be the vast m...  ...  why would young fighting age men be the vast m...
2  @KamalaHarris Illegals Dump their Kids at the ...  ...   illegals dump their kids at the border like r...
3  NY Times: 'Nearly All White' States Pose 'an A...  ...  ny times: 'nearly all white' states pose 'an a...
4  Orban in Brussels: European leaders are ignori...  ...  orban in brussels: european leaders are ignori...

[5 rows x 3 columns]

REMOVE PUNCTUATIONS

In [ ]:
# drop the new column created in last cell
#df.drop(["text_lower"], axis=1, inplace=True)

PUNCT_TO_REMOVE = string.punctuation
def remove_punctuation(text):
    """custom function to remove the punctuation"""
    return text.translate(str.maketrans('', '', PUNCT_TO_REMOVE))

df["text_wo_punct"] = df['text_lower'].apply(lambda text: remove_punctuation(text))
df.head()

text  ...                                      text_wo_punct
0  Hurray, saving us $$$ in so many ways @potus @...  ...  hurray saving us  in so many ways   lockthemup...
1  Why would young fighting age men be the vast m...  ...  why would young fighting age men be the vast m...
2  @KamalaHarris Illegals Dump their Kids at the ...  ...   illegals dump their kids at the border like r...
3  NY Times: 'Nearly All White' States Pose 'an A...  ...  ny times nearly all white states pose an array...
4  Orban in Brussels: European leaders are ignori...  ...  orban in brussels european leaders are ignorin...

[5 rows x 4 columns]

STOPWORDS

In [ ]:
!pip install nltk

In [ ]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [ ]:
from nltk.corpus import stopwords
", ".join(stopwords.words('english'))


"i, me, my, myself, we, our, ours, ourselves, you, you're, you've, you'll, you'd, your, yours, yourself, yourselves, he, him, his, himself, she, she's, her, hers, herself, it, it's, its, itself, they, them, their, theirs, themselves, what, which, who, whom, this, that, that'll, these, those, am, is, are, was, were, be, been, being, have, has, had, having, do, does, did, doing, a, an, the, and, but, if, or, because, as, until, while, of, at, by, for, with, about, against, between, into, through, during, before, after, above, below, to, from, up, down, in, out, on, off, over, under, again, further, then, once, here, there, when, where, why, how, all, any, both, each, few, more, most, other, some, such, no, nor, not, only, own, same, so, than, too, very, s, t, can, will, just, don, don't, should, should've, now, d, ll, m, o, re, ve, y, ain, aren, aren't, couldn, couldn't, didn, didn't, doesn, doesn't, hadn, hadn't, hasn, hasn't, haven, haven't, isn, isn't, ma, mightn, mightn't, mustn, mus

In [ ]:
STOPWORDS = set(stopwords.words('english'))
def remove_stopwords(text):
    """custom function to remove the stopwords"""
    return " ".join([word for word in str(text).split() if word not in STOPWORDS])

df["text_wo_stop"] = df["text_wo_punct"].apply(lambda text: remove_stopwords(text))
df.head()

text  ...                                       text_wo_stop
0  Hurray, saving us $$$ in so many ways @potus @...  ...  hurray saving us many ways lockthemup buildthe...
1  Why would young fighting age men be the vast m...  ...  would young fighting age men vast majority one...
2  @KamalaHarris Illegals Dump their Kids at the ...  ...  illegals dump kids border like road kill refus...
3  NY Times: 'Nearly All White' States Pose 'an A...  ...  ny times nearly white states pose array proble...
4  Orban in Brussels: European leaders are ignori...  ...  orban brussels european leaders ignoring peopl...

[5 rows x 5 columns]

REMOVE URLS

In [ ]:
def remove_urls(text):
    url_pattern = re.compile(r'https?://\S+|www\.\S+')
    return url_pattern.sub(r'', text)

In [ ]:
df["text_wo_urlno"] = df["text_wo_stop"].apply(lambda text: remove_urls(text))
df.head()

text  ...                                      text_wo_urlno
0  Hurray, saving us $$$ in so many ways @potus @...  ...  hurray saving us many ways lockthemup buildthe...
1  Why would young fighting age men be the vast m...  ...  would young fighting age men vast majority one...
2  @KamalaHarris Illegals Dump their Kids at the ...  ...  illegals dump kids border like road kill refus...
3  NY Times: 'Nearly All White' States Pose 'an A...  ...  ny times nearly white states pose array proble...
4  Orban in Brussels: European leaders are ignori...  ...  orban brussels european leaders ignoring peopl...

[5 rows x 6 columns]

REMOVE HTML TAGS

In [ ]:
def remove_html(text):
    html_pattern = re.compile('<.*?>')
    return html_pattern.sub(r'', text)

df["text_wo_htmlno"] = df["text_wo_urlno"].apply(lambda text: remove_html(text))
df.head()


text  ...                                     text_wo_htmlno
0  Hurray, saving us $$$ in so many ways @potus @...  ...  hurray saving us many ways lockthemup buildthe...
1  Why would young fighting age men be the vast m...  ...  would young fighting age men vast majority one...
2  @KamalaHarris Illegals Dump their Kids at the ...  ...  illegals dump kids border like road kill refus...
3  NY Times: 'Nearly All White' States Pose 'an A...  ...  ny times nearly white states pose array proble...
4  Orban in Brussels: European leaders are ignori...  ...  orban brussels european leaders ignoring peopl...

[5 rows x 7 columns]

REMOVE DIGITS

In [ ]:
#df['text_wo_digitno'] = df['text_wo_urlno'].apply(lambda x: re.sub('W*dw*','',x))
#df.head()

In [ ]:
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

LEMMATIZATION

In [ ]:
nltk.download('averaged_perceptron_tagger')
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer

lemmatizer = WordNetLemmatizer()
wordnet_map = {"N":wordnet.NOUN, "V":wordnet.VERB, "J":wordnet.ADJ, "R":wordnet.ADV}
def lemmatize_words(text):
    pos_tagged_text = nltk.pos_tag(text.split())
    return " ".join([lemmatizer.lemmatize(word, wordnet_map.get(pos[0], wordnet.NOUN)) for word, pos in pos_tagged_text])

df["text_lemmatized"] = df["text_wo_htmlno"].apply(lambda text: lemmatize_words(text))
df.head()

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


text  ...                                    text_lemmatized
0  Hurray, saving us $$$ in so many ways @potus @...  ...  hurray save u many way lockthemup buildthewall...
1  Why would young fighting age men be the vast m...  ...  would young fight age men vast majority one es...
2  @KamalaHarris Illegals Dump their Kids at the ...  ...  illegals dump kid border like road kill refuse...
3  NY Times: 'Nearly All White' States Pose 'an A...  ...  ny time nearly white state pose array problem ...
4  Orban in Brussels: European leaders are ignori...  ...  orban brussels european leader ignore people w...

[5 rows x 8 columns]

In [ ]:
lemmatizer.lemmatize("running")


'running'

In [ ]:
df['text_lemmatized'].to_list
print(type(df['text_lemmatized']))
input = df['text_lemmatized']
input = input.tolist()
print(type(input))
print(len(input))
print(input)

<class 'pandas.core.series.Series'>
<class 'list'>
9000
['hurray save u many way lockthemup buildthewall enddaca boycottnfl boycottnike', 'would young fight age men vast majority one escape war amp cannot fight like woman child elderlyits majority refugees actually refugees economic migrant try get europe', 'illegals dump kid border like road kill refuse unite hope get amnesty free education welfare illegal familesbelongtogether country taxpayer dime scam nodaca noamnesty sendthe', 'ny time nearly white state pose array problem immigrant', 'orban brussels european leader ignore people want migrant', 'legal illegal buildthatwall', 'antifa pack druggie misfits one love violent thug cry attention hit self importancejuveniledelinquents', 'exteacher pleads guilty rape charge', 'still place bengali sylheti class london 2nd language know anyone interested', 'dfid africa regional profile july 2018', 'watch benjamin netanyahu back trump decision cut aid palestinian unrwa free speech time', 'ill

In [ ]:
import numpy as np 
import nltk 
#nltk.download('gutenberg')

class cbow:
	
	def __init__(self, text, window=2, n=4, learning_rate=0.0001):
		"""
		Initialize a new model for the current dataset. 
		"""
		self.n = n																																	# desired size of the word vectors
		self.text = text								 
		self.window = window								
		self.learning_rate = learning_rate						 
		self.vocabulary = list(set(text.lower().split()))
		self.word_index = {k: v for v, k in enumerate(self.vocabulary)}             # generate index for each word in the vocabulary 
		self.V = np.random.uniform(-0.001, 0.001,  (n, len(self.vocabulary))) 	    # input vector matrix for each word ( n X |V| )
		self.U = np.random.uniform(-0.001, 0.001 , (len(self.vocabulary), n)) 	    # output vector matrix for each word ( |V| X n )
		print("Word vec size = %s " % self.n)
		print("Vocabulary size = %s " % self.vocabulary)
		print("Word Index dict = %s " % self.word_index)
		print("Shape of V = %s " + str(self.V.shape))
		print("Shape of U = %s " + str(self.U.shape))
		#print("V matrix = %s " + str(self.V))
		#print("U matrix = %s " + str(self.U))

	def get_one_hot(self, index):
		one_hot = np.zeros(len(self.vocabulary))
		one_hot[index] = 1
		return one_hot 

	def get_representation_from_onehot(self, one_hot=None):
		temp = np.dot(self.V, one_hot)
		return temp

	def get_average_vector_context(self, left_context=None, right_context=None):
		avg_vector = np.zeros(self.n)

		for word in left_context:							
			current_word_index = self.word_index[word]				
			one_hot_encoding = self.get_one_hot(current_word_index) 		
			avg_vector += self.get_representation_from_onehot(one_hot=one_hot_encoding)

		for word in right_context:						
			current_word_index = self.word_index[word]
			one_hot_encoding = self.get_one_hot(current_word_index)
			avg_vector += self.get_representation_from_onehot(one_hot=one_hot_encoding)

		avg_vector = avg_vector/( 2 * self.window )
		return avg_vector

	def get_score(self, avg_vec=None):
		"""
		Given an averaged vector in the current context of the 
		center word, compute the product of the U with avg_vec.
		"""
		#print("U shape = " + str(self.U.shape))
		#print("Average vector shape = " + str(avg_vec.shape))
		return np.dot(self.U, avg_vec)

	def softmax(self, x):
		if x.ndim > 1:
        		x -= np.max(x, axis=1).reshape(-1, 1)
        		x = np.exp(x)/np.sum(np.exp(x), axis=1).reshape(-1, 1)
		else:
        		x -= np.max(x)
        		x = np.exp(x)/np.sum(np.exp(x))
		return x

	def compute_cross_entropy_error(self, y, y_hat):
		return -y * np.log(y_hat)

	def compute_EH(self, error):	
		EH = np.zeros(self.n)
		for i in range(self.n):
			temp = 0.0
			for j in range(len(self.vocabulary)):
				temp += error[j] * self.U[j, i]
			EH[i] = temp 
		return EH

	def update_U(self, error, avg_vec):
		"""
		Given the cross entropy error occured in the current 
		sample, this function updates the U matrix. 
		"""
		for i in range(self.U.shape[0]):
			self.U[i, :] -= self.learning_rate * error[i] * avg_vec
		
	def update_V(self, error, left_context, right_context):
		"""
		This function updates the V matrix 
		"""
		# Compute EH term 
		EH = self.compute_EH(error)
		
		# pass the update 
		for word in left_context + right_context:
			current_word_index = self.word_index[word]
			self.V[:, current_word_index] -= ( 2 * self.window ) * self.learning_rate * EH

	def fit(self):
		self.split_text = self.text.lower().split()
		for i in range(len(self.split_text)):
			#print("\n")
			center_word = self.split_text[i]								# centre word in the current context  
			if i - self.window < 0:
				left_window, right_window = self.split_text[:i], self.split_text[i+1:i+self.window]   	# left context and right context 
			else:
				left_window, right_window = self.split_text[i-self.window:i], self.split_text[i+1:i+self.window]	

			#print("Center word = %s, left_window = %s & right_window=%s" % (center_word, left_window, right_window))

			# Compute the avg vector using the left and right context 	
			avg_vector = self.get_average_vector_context(left_context=left_window, \
								     right_context=right_window)							
			
			# Get score 
			x_hat = self.get_score(avg_vector)
			#print("x_hat shape = " + str(x_hat.shape))

			# Get softmax 
			y_hat = self.softmax(x_hat)

			# Get the 1 - hot representation of the center word
			center_word_index = self.word_index[center_word]
			center_word_one_hot_encoding = self.get_one_hot(center_word_index)

			# Compute the error in prediction for the current center word 
			error = self.compute_cross_entropy_error(center_word_one_hot_encoding, y_hat)
			#print("Error = %s" % error)

			# Update U matrix 
			self.update_U(error=error, avg_vec=avg_vector)

			# Update V marix 
			self.update_V(error=error, left_context=left_window, right_context=right_window)

		# Final U matrix 
		#print("Final U matrix = %s " + str(self.U))

		# Final V matrix
		#print("Final V matrix = %s " + str(self.V))


'''text = nltk.corpus.gutenberg.words('austen-emma.txt')
text = ' '.join(text[:100])'''

l = len(input)
word_vec_dict = {}
word_vec_arr = []
for i in range(l):
	model  = cbow(text=input[i])
	model.fit()

	word_vec_sent_arr = []
	final_vectors = {}
	for k, v in model.word_index.items():
		#print(np.dot(model.V, model.get_one_hot(model.word_index[k])))\
		final_vectors[k] = model.V[:, v]
		word_vec_dict.update(final_vectors)
		word_vec_sent_arr.append(model.V[:, v].tolist())
	word_vec_arr.append(word_vec_sent_arr)

print(word_vec_dict)
print(len(word_vec_arr[0][0]))

Streaming output truncated to the last 5000 lines.
Word Index dict = {'somebody': 0, 'hump': 1, 'day': 2, 'say': 3, 'happy': 4} 
Shape of V = %s (4, 5)
Shape of U = %s (5, 4)
Word vec size = 4 
Vocabulary size = ['start', 'im', 'mind', 'dont', 'wait', '🌚', 'rant'] 
Word Index dict = {'start': 0, 'im': 1, 'mind': 2, 'dont': 3, 'wait': 4, '🌚': 5, 'rant': 6} 
Shape of V = %s (4, 7)
Shape of U = %s (7, 4)
Word vec size = 4 
Vocabulary size = ['although', 'well', 'people', 'think', 'dont', 'actually', 'meet', 'tweet', 'place', 'might', 'weve', 'see'] 
Word Index dict = {'although': 0, 'well': 1, 'people': 2, 'think': 3, 'dont': 4, 'actually': 5, 'meet': 6, 'tweet': 7, 'place': 8, 'might': 9, 'weve': 10, 'see': 11} 
Shape of V = %s (4, 12)
Shape of U = %s (12, 4)
Word vec size = 4 
Vocabulary size = ['much', 'realize', 'public', 'really', 'pool', 'hate', 'fuck', 'make', 'kid'] 
Word Index dict = {'much': 0, 'realize': 1, 'public': 2, 'really': 3, 'pool': 4, 'hate': 5, 'fuck': 6, 'make': 7, '

In [ ]:
from sklearn.model_selection import train_test_split
Y = full_df['HS']
Y = Y.values.tolist()
print(Y)
print(type(Y))
print(test_X)
train_X, test_X, train_Y, test_Y = train_test_split(word_vec_arr,Y,test_size=0.2)

for i in range(len(train_X)):
  train_X[i] = np.nanmean(train_X[i], axis=0).tolist()
for i in range(len(test_X)):
  test_X[i] = np.nanmean(test_X[i], axis=0).tolist()

print(test_X)

[1, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 1, 1, 0, 0, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: RuntimeWarning: Mean of empty slice
  # Remove the CWD from sys.path while we load stuff.


[[0.00010717109903070153, -0.000187643058293914, -0.00024382556318624442, -8.801309007457886e-05], [0.000260138488218598, -6.525410387340543e-06, 5.085883123706115e-05, -0.0003976029357352046], [0.0003396768380394914, 9.282015630812743e-05, -0.00013031312593024977, 0.0004482696972170905], [-6.073214464537838e-05, 9.213064863892854e-05, -0.00028651012174295466, -0.000127894877995025], [0.00010766260438088442, -0.00028357664567454585, -8.145117423541062e-05, 4.43779762753286e-05], [0.00014261932559681988, 0.00015057553745987108, -0.0003835305099032233, 4.0535270451389166e-05], [-5.7336435566348534e-05, 2.068515156417342e-05, -0.00020413829026794816, 0.00011135917125749824], [1.4856391901777208e-05, 9.346883693863006e-05, -0.00017256547722489985, 1.3170871555465233e-05], [7.557447078307175e-05, -0.0004489704192318785, -0.000144297638774738, 0.00010819767638932062], [3.1669836364092015e-05, 2.3574370256976295e-05, 0.00015175203472936468, -1.210469226184287e-05], [-0.000366839715782843, 5.6